In [2]:
import pandas as pd
import numpy as np
import json
import sqlite3
from quizzes import process_quiz

db_file = 'progsnap2_21_consenting.db'
NUM_QUIZ_INCLUDE = 10

# Subject table
df_LinkSubject = pd.read_sql(f"""
SELECT * FROM LinkSubject
""", sqlite3.connect(db_file))

# Assignment table
df_LinkAssignment = pd.read_sql(f"""
SELECT * FROM LinkAssignment
""", sqlite3.connect(db_file))

In [3]:
# Split students' final grade into high and low based on the median
df_high_low = df_LinkSubject[['SubjectID', 'X-FinalTotalScore']]
df_high_low['HighLow'] = (df_high_low['X-FinalTotalScore'] > df_high_low['X-FinalTotalScore'].median()).astype(int)
df_high_low

C:\Users\mianh\AppData\Local\Temp/ipykernel_23580/871373944.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_high_low['HighLow'] = (df_high_low['X-FinalTotalScore'] > df_high_low['X-FinalTotalScore'].median()).astype(int)


SubjectID  X-FinalTotalScore  HighLow
0         630              92.14        1
1         638              97.62        1
2         571              75.32        0
3         575              91.97        1
4         617              65.50        0
..        ...                ...      ...
99        637              97.17        1
100       633              74.80        0
101       815              37.80        0
102       737              24.89        0
103       509              46.75        0

[104 rows x 3 columns]

In [4]:
# Get subject ID, 295
list_subjectID = df_LinkSubject.loc[:,'SubjectID']

# Get quiz ID, 384 388 434
list_quizID = df_LinkAssignment.loc[df_LinkAssignment['X-Name'].str.contains('Quiz'), 'AssignmentId']
list_quizID = list_quizID[:NUM_QUIZ_INCLUDE]

In [5]:
# Filter first 10 quizzes, with all subject ID
subject_query = ("'" + list_subjectID + "'").to_string(index=False).replace('\n',',')
quiz_query = ("'" + list_quizID + "'").to_string(index=False).replace('\n',',')

df_quiz = pd.read_sql(f"""
SELECT MainTable.SubjectID, MainTable.AssignmentID, `X-Instructions` as Instructions, `X-Code.OnRun` as OnRun, Contents, EventType
FROM MainTable, CodeState, LinkAssignment
WHERE CodeState.ID = MainTable.CodeStateID
AND MainTable.CodeStateID != '0'
AND MainTable.AssignmentID in ({quiz_query})
AND MainTable.SubjectID in ({subject_query})
AND LinkAssignment.AssignmentID = MainTable.AssignmentID
""", sqlite3.connect(db_file))
df_quiz

SubjectID AssignmentID  \
0           577          384   
1           577          384   
2           577          384   
3           577          384   
4           577          384   
...         ...          ...   
32816       808          345   
32817       808          345   
32818       808          345   
32819       808          345   
32820       808          345   

                                            Instructions  \
0      {"questions":{"Define Computer Science":{"type...   
1      {"questions":{"Define Computer Science":{"type...   
2      {"questions":{"Define Computer Science":{"type...   
3      {"questions":{"Define Computer Science":{"type...   
4      {"questions":{"Define Computer Science":{"type...   
...                                                  ...   
32816  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32817  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32818  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32819  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32820  {\n  "questions": {\n    "ArithmeticOperatorPr...   

                                                   OnRun  \
0      {"questions":{"Define Computer Science":{"corr...   
1      {"questions":{"Define Computer Science":{"corr...   
2      {"questions":{"Define Computer Science":{"corr...   
3      {"questions":{"Define Computer Science":{"corr...   
4      {"questions":{"Define Computer Science":{"corr...   
...                                                  ...   
32816  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32817  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32818  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32819  {\n  "questions": {\n    "ArithmeticOperatorPr...   
32820  {\n  "questions": {\n    "ArithmeticOperatorPr...   

                                                Contents         EventType  
0      b'{\n  "studentAnswers": {\n    "Define Comput...         File.Edit  
1      b'{\n  "studentAnswers": {\n    "Define Comput...         File.Edit  
2      b'{\n  "studentAnswers": {\n    "Define Comput...         File.Edit  
3      b'{\n  "studentAnswers": {\n    "Define Comput...         File.Edit  
4      b'{\n  "studentAnswers": {\n    "Define Comput...         File.Edit  
...                                                  ...               ...  
32816  b'{\n  "studentAnswers": {\n    "ArithmeticOpe...  X-Submission.LMS  
32817  b'{\n  "studentAnswers": {\n    "ArithmeticOpe...         File.Edit  
32818  b'{\n  "studentAnswers": {\n    "ArithmeticOpe...         File.Edit  
32819  b'{\n  "studentAnswers": {\n    "ArithmeticOpe...         File.Edit  
32820  b'{\n  "studentAnswers": {\n    "ArithmeticOpe...  X-Submission.LMS  

[32821 rows x 6 columns]

In [6]:
pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)

In [7]:
for index in range(9):
    df_single_quiz = df_quiz.loc[df_quiz['AssignmentID'].str.contains(list_quizID.iloc[index])].reset_index()
    results = df_single_quiz.apply(lambda row: 
        vars(process_quiz(json.loads(row.Instructions),
                          json.loads(row.OnRun),
                          json.loads(row.Contents.decode('utf-8') or "{}"))),
        axis=1
    )
    aaa = pd.json_normalize(results)
    matching = [s for s in list(aaa.columns) if ".score" in s]
    bbb = aaa.loc[:,matching]
    bbb = bbb.astype(float)
    bbb = bbb.fillna(0).astype(float)

    df_single_quiz_state = pd.concat([df_single_quiz[['SubjectID']], bbb], axis=1)
    df_single_quiz_state
    f_high = open("quiz"+str(index+1)+"_high.txt", "a")
    f_low = open("quiz"+str(index+1)+"_low.txt", "a")
    f_id = open("quiz"+str(index+1)+"_id.txt", "a")
    m=1
    n=1
    for j in range(len(list_subjectID)):
        ccc = df_single_quiz_state.loc[
            df_single_quiz_state['SubjectID'].str.contains(list_subjectID[j]), 
            matching].to_numpy()
        np.set_printoptions(formatter={'float': '{: 0.1f}'.format})
        if(df_high_low.loc[j, 'HighLow'] == 1):
            print('subject id is high', list_subjectID[j])
            f_id.write('high '+ list_subjectID[j] + '\n')
            f_high.write('s'+str(m)+' '+np.array2string(ccc).replace('  ', '_').replace(']\n [', '')[3:-2] + '\n')
            m=m+1
        else:
            print('subject id is low', list_subjectID[j])
            f_id.write('low '+ list_subjectID[j] + '\n')
            f_low.write('s'+str(n)+' '+np.array2string(ccc).replace('  ', '_').replace(']\n [', '')[3:-2] + '\n')
            n=n+1
    f_high.close()
    f_low.close()
    f_id.close()

score  correct  points_possible  graded_successfully error  \
0     0.472727    False             11.0                 True  None   
1     0.563636    False             11.0                 True  None   
2     0.654545    False             11.0                 True  None   
3     0.563636    False             11.0                 True  None   
4     0.654545    False             11.0                 True  None   
5     0.684848    False             11.0                 True  None   
6     0.715152    False             11.0                 True  None   
7     0.745455    False             11.0                 True  None   
8     0.800000    False             11.0                 True  None   
9     0.854545    False             11.0                 True  None   
10    0.800000    False             11.0                 True  None   
11    0.854545    False             11.0                 True  None   
12    0.909091    False             11.0                 True  None   
13    1.000000     True             11.0                 True  None   
14    0.909091    False             11.0                 True  None   
15    0.909091    False             11.0                 True  None   
16    0.909091    False             11.0                 True  None   
17    0.909091    False             11.0                 True  None   
18    1.000000     True             11.0                 True  None   
19    1.000000    False             11.0                 True  None   
20    1.000000    False             11.0                 True  None   
21    0.472727    False             11.0                 True  None   
22    0.563636    False             11.0                 True  None   
23    0.654545    False             11.0                 True  None   
24    0.745455    False             11.0                 True  None   
25    0.775758    False             11.0                 True  None   
26    0.806061    False             11.0                 True  None   
27    0.836364    False             11.0                 True  None   
28    0.890909    False             11.0                 True  None   
29    0.945455    False             11.0                 True  None   
30    1.000000     True             11.0                 True  None   
31    1.000000     True             11.0                 True  None   
32    1.000000     True             11.0                 True  None   
33    1.000000    False             11.0                 True  None   
34    1.000000    False             11.0                 True  None   
35    0.472727    False             11.0                 True  None   
36    0.472727    False             11.0                 True  None   
37    0.563636    False             11.0                 True  None   
38    0.654545    False             11.0                 True  None   
39    0.745455    False             11.0                 True  None   
40    0.775758    False             11.0                 True  None   
41    0.806061    False             11.0                 True  None   
42    0.836364    False             11.0                 True  None   
43    0.890909    False             11.0                 True  None   
44    0.945455    False             11.0                 True  None   
45    0.945455    False             11.0                 True  None   
46    0.890909    False             11.0                 True  None   
47    0.945455    False             11.0                 True  None   
48    1.000000    False             11.0                 True  None   
49    1.000000    False             11.0                 True  None   
50    1.000000     True             11.0                 True  None   
51    0.909091    False             11.0                 True  None   
52    1.000000     True             11.0                 True  None   
53    1.000000     True             11.0                 True  None   
54    1.000000     True             11.0                 True  None   
55    1.000000    False          